In [1]:
!pip install pennylane
!pip install jax

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.1/57.1 kB 1.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.3/5.3 MB 65.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 934.3/934.3 kB 52.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 73.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 60.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 167.9/167.9 kB 8.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.6/8.6 MB 68.1 MB/s eta 0:00:00


In [2]:
import pennylane as qml

dev = qml.device("default.qubit", wires=2)

@qml.qnode(dev)
def circuit(param):
    qml.RX(param, wires=0)
    qml.CNOT(wires=[0, 1])

    return qml.expval(qml.PauliZ(1))

In [ ]:
import jax
import jax.numpy as jnp
from jax import random, grad

# data
key = random.PRNGKey(42)
x = random.normal(key, (10, 3))
y = jnp.array([[1.0], [0.0], [1.0], [0.0], [1.0],
               [0.0], [1.0], [0.0], [1.0], [0.0]])

# init weights
def init_params(key):
    k1, k2 = random.split(key)
    W1 = random.normal(k1, (3, 4))
    b1 = jnp.zeros(4)
    W2 = random.normal(k2, (4, 1))
    b2 = jnp.zeros(1)
    return (W1, b1, W2, b2)

# model
def forward(params, x):
    W1, b1, W2, b2 = params
    h = jnp.tanh(x @ W1 + b1)
    h = jax.nn.sigmoid(h @ W2 + circuit(b2 * jnp.pi))
    return h


# loss
def loss_fn(params, x, y):
    preds = forward(params, x)
    return jnp.mean((preds - y) ** 2)

# training step
@jax.jit
def update(params, x, y, lr=0.1):
    grads = grad(loss_fn)(params, x, y)
    return jax.tree_util.tree_map(lambda p, g: p - lr * g, params, grads)

# train
params = init_params(key)
for i in range(200):
    params = update(params, x, y)
    if i % 5 == 0:
        print(i, loss_fn(params, x, y))


0 0.30217844
5 0.29236612
10 0.2849971
15 0.27915093
20 0.27423224
25 0.26988873
30 0.26590854
35 0.26215717
40 0.25854278
45 0.25499853
50 0.2514727
55 0.24792306
60 0.2443141
65 0.24061473
70 0.23679791
75 0.23283985
80 0.22872034
85 0.2244227
90 0.21993451
95 0.21524821
100 0.21036112
105 0.20527649
110 0.2000031
115 0.19455588
120 0.188955
125 0.18322562
130 0.17739694
135 0.17150114
140 0.16557209
145 0.15964386
150 0.1537499
155 0.14792159
160 0.14218764
165 0.13657312
170 0.13109954
175 0.12578449
180 0.12064164
185 0.11568117
190 0.110910036
195 0.10633228


In [ ]:
forward(params, x[0,:])

Array([0.8505869], dtype=float32)